# Jupyter Notebook for Interactive Labeling
______

This Jupyter Notebook combines a manual and automated labeling technique.
It includes a basic implementation of Multinomial Bayes Classifier.
By calculating estimated class probabilities, we decide whether a news article has to be labeled manually or can be labeled automatically.
For multiclass labeling, 3 classes are used.
  
Please note: User instructions are written in upper-case.
__________
Version: 2019-02-28, Anne Lorenz

In [1]:
import csv
import operator
import pickle
import random

from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
from IPython.core.interactiveshell import InteractiveShell
from IPython.display import display
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_selection import SelectPercentile
from sklearn.metrics import recall_score, precision_score, f1_score, make_scorer
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import StratifiedKFold
from sklearn.pipeline import Pipeline
from sklearn.naive_bayes import MultinomialNB
from sklearn.semi_supervised import label_propagation

from BagOfWords import BagOfWords
from MNBInteractive import MNBInteractive
from MultinomialNaiveBayes import MultinomialNaiveBayes

## Part I: Data preparation

First, we import our data set of 10 000 business news articles from a csv file.
It contains 833/834 articles of each month of the year 2017.
For detailed information regarding the data set, please read the full documentation.

In [2]:
# initialize random => reproducible sequence
random.seed(5)

filepath = '../data/cleaned_data_set_without_header.csv'

# set up wider display area
pd.set_option('display.max_colwidth', -1)

# show full text for print statement
InteractiveShell.ast_node_interactivity = "all"

We load the previously created dictionary of all article indices (keys) with a list of mentioned organizations (values).
In the following, we limit the number of occurences of a certain company name in all labeled articles to 3 to avoid imbalance.

PLEASE INSERT M MANUALLY IF PROCESS HAS BEEN INTERRUPTED BEFORE.

In [8]:
m=16

In [9]:
# read current data set from csv
df = pd.read_csv('../data/interactive_labeling_round_{}_temp.csv'.format(m),
          sep='|',
          usecols=range(1,13), # drop first column 'unnamed'
          encoding='utf-8',
          quoting=csv.QUOTE_NONNUMERIC,
          quotechar='\'')

# find current iteration/round number
m = int(df['Round'].max())
print('This round number: {}'.format(m))
print('Number of manually labeled articles: {}'.format(len(df.loc[df['Label'] != -1])))
print('Number of manually unlabeled articles: {}'.format(len(df.loc[df['Label'] == -1])))

This round number: 16
Number of manually labeled articles: 1132
Number of manually unlabeled articles: 8868


START:

Building the training data set using stratified sampling:

In [5]:
m = 0

In [6]:
# iteration number
m

0

In [7]:
#set_0 = df.loc[(df['Round'] < m) & (df['Label'] == 0)]
#set_1 = df.loc[(df['Round'] < m) & (df['Label'] == 1)]
#set_2 = df.loc[(df['Round'] < m) & (df['Label'] == 2)]

In [8]:
strat_len = min(len(set_0), len(set_1), len(set_2))
len(set_0)
len(set_1)
len(set_2)
strat_len

84

3

13

3

In [9]:
# neu für CV: 
#training_data = df.loc[(df['Round'] < m)]

Uuid  \
9819  05581b3fad7dde79fb4a44ab11400222423903a7   
850   d6970501f4180455abb50f120d4f0c1da7818c2a   
3242  41dfed3520e939bff77261f50947154ace5b0a77   

                                                                              Title  \
9819  CANADA STOCKS-TSX posts record high as energy, marijuana company shares climb   
850   UPDATE 1-Russia's Detsky Mir prices IPO at bottom of range-sources              
3242  Takata rescue talks extended, even as bankruptcy risk looms                     

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 Text  \
9819  December 27, 2017 / 9:52 PM / in 8 mi

Uuid  \
2730  9f6bd526a9c9c9305b18b4d121d723ac878012ef   
4043  04e51a867745700ec080b4e17618d8c37bfe4122   
5950  4dde03a74e2ac98954002bfc960a5f1d60182649   

                                                             Title  \
2730  LVMH's Arnault to take full control of Christian Dior          
4043  EU mergers and takeovers (May 19)                              
5950  Canada's OneREIT to be taken private in a C$1.1 billion deal   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

Uuid  \
4352  752df0da1a3ecf70f57c017b798b2ceff37f557a   
1672  476ed99eb49bd466258784067ac62dd7815e05ab   
5052  370eed1e30c0117362432816475315a18ab67463   

                                                                           Title  \
4352  FTC to advise blocking Walgreens deal to buy Rite Aid - CNBC                 
1672  UPDATE 1-Hansteen to sell German, Dutch industrial properties for $1.4 bln   
5052  Italy could consider taking small stake in Alitalia - minister               

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                Text  \
4352  June 9 Regulatory authorities are set to advise blocking U.S. drugstore chain Walgreens Boots Alliance Inc's deal to buy smaller rival Rite Aid Corp, CNBC reported on Friday, citing a report.The companies have been waiting for a year-and-a-half for approval from the Federal Trade Commission (FTC) since the initial offer made in 2015.In that time, the closing date of the deal has been postponed repeatedly and the offer price reduced to $6.50 to $7.00 per Rite Aid share, down from $9.The deal would have helped Walgreens widen its U.S. footprint and negotiate for lower drug costs. (Reporting by Sruthi Ramakrishnan in Bengaluru; Editing by Shounak Dasgupta)                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             

[9819.0, 850.0, 3242.0, 2730.0, 4043.0, 5950.0, 4352.0, 1672.0, 5052.0]

In [ ]:
# testing data: manually labeled articles of current round
testing_data = df.loc[(df['Round'] == m)]
len(testing_data)

In [ ]:
# classical model fitting:

# all labeled as samples
#training_data = pd.concat([set_0, set_1, set_2])

#m += 1
#m

# classical model fitting:
#all_labeled_data = df.loc[(df['Round'] <= m)].reset_index()
#recall_scores, precision_scores, f1_scores = MultinomialNaiveBayes.make_mnb(all_labeled_data)
#recall_score = sum(recall_scores)/len(recall_scores)
#print('recall: {}'.format(recall_score))
#precision_score = sum(precision_scores)/len(precision_scores)
#print('precision: {}'.format(precision_score))
#f1_score = sum(f1_scores)/len(f1_scores)
#print('f1 score: {}'.format(f1_score))

# stratified sampled:
#training_data = pd.concat([set_0[:strat], set_1[:strat], set_2[:strat]])

#len(training_data)

We now check (and correct if necessary) the next auto-labeled articles.

## Multinomial Naive Bayes Classification: ##

In [ ]:
# use sklearn's CountVectorizer
# cv = False
cv = True

# call script with manually labeled and manually unlabeled samples
%time classes, class_count, class_probs = MNBInteractive.estimate_mnb(training_data, testing_data, cv)

In [ ]:
m

In [ ]:
# annotate highest estimated probability for every instance
maxima = []

for row in class_probs:
    maxima.append(np.amax(row))

In [ ]:
#maxima

In [ ]:
# save class_probs array
#with open('../obj/'+ 'array_class_probs_round_{}_stratified'.format(m) + '.pkl', 'wb') as f:
    pickle.dump(maxima, f, pickle.HIGHEST_PROTOCOL)

In [ ]:
# sort list in descending order
maxima.sort(reverse=True)

# convert list to array
probas = np.asarray(maxima)

n_bins = 50

fig, ax = plt.subplots(figsize=(8, 4))

# plot the cumulative histogram
n, bins, patches = ax.hist(probas, n_bins, density=1, histtype='step',
                           cumulative=True, facecolor='darkred')

ax.grid(True)
#ax.set_title('Cumulative distribution of highest estimated probability')
ax.set_xlabel('Highest estimated probability')
ax.set_ylabel('Fraction of articles with this highest estimated probability')
#plt.axis([0.5, 1, 0, 0.02])
#ax.set_xbound(lower=0.5, upper=0.99)
plt.show()

In [ ]:
plt.savefig('..\\visualization\\proba_after_round_{}_stratified.png'.format(m))

We annotate each article's estimated class with its probability in columns 'Estimated' and 'Probability':

In [ ]:
# series of indices of recently estimated articles 
indices_estimated = df.loc[df['Round'] == m, 'Index'].tolist()

n = 0    
for row in class_probs:
    for i in range(0, len(classes)):
        index = indices_estimated[n]
        # save estimated label
        if np.amax(row) == row[i]:
            df.loc[index, 'Estimated'] = classes[i]
            # annotate probability
            df.loc[index, 'Probability'] = row[i]
    n += 1

In [10]:
m = 16

In [11]:
print('###############')
zero_0 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 0) & (df['Label'] == 0)])
zero_0
zero_1 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 0) & (df['Label'] == 1)])
zero_1
zero_2 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 0) & (df['Label'] == 2)])
zero_2
print('###############')
one_0 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 1) & (df['Label'] == 0)])
one_0
one_1 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 1) & (df['Label'] == 1)])
one_1
one_2 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 1) & (df['Label'] == 2)])
one_2
print('###############')

two_0 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 2) & (df['Label'] == 0)])
two_0
two_1 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 2) & (df['Label'] == 1)])
two_1
two_2 = len(df.loc[(df['Round'] == m) & (df['Estimated'] == 2) & (df['Label'] == 2)])
two_2
print('###############')

total = zero_0 + zero_1 + zero_2 + one_0 + one_1 + one_2 + two_0 + two_1 + two_2

tp_0 = zero_0
tp_0
tn_0 = one_1 + one_2 + two_1 + two_2
tn_0
fp_0 = zero_1 + zero_2
fp_0
fn_0 = one_0 + two_0
fn_0
print('###############')

tp_1 = one_1
tp_1
tn_1 = zero_0 + zero_2 + two_0 + two_2
tn_1
fp_1 = one_0 + one_2
fp_1
fn_1 = zero_1 + two_1
fn_1
print('###############')

tp_2 = two_2
tp_2
tn_2 = zero_0 + zero_1 + one_0 + one_1
tn_2
fp_2 = two_0 + two_1
fp_2
fn_2 = zero_2 + one_2
fn_2
print('###############')

prec_0 = tp_0 / (tp_0 + fp_0) * 100
prec_0
rec_0 = tp_0 / (tp_0 + fn_0) * 100
rec_0
acc_0 = (tp_0 + tn_0) / total * 100
acc_0
print('###############')

prec_1 = tp_1 / (tp_1 + fp_1) * 100
prec_1
rec_1 = tp_1  / (tp_1 + fn_1) * 100
rec_1
acc_1 = (tp_1 + tn_1) / total * 100
acc_1
print('###############')

prec_2 = tp_2 / (tp_2 + fp_2) * 100
prec_2
rec_2 = tp_2 / (tp_2 + fn_2) * 100
rec_2
acc_2 = (tp_2 + tn_2) / total * 100
acc_2
print('###############')

(prec_1 + prec_2 + prec_0) / 3
(rec_1 + rec_2 + rec_0) / 3
(acc_1 + acc_2 + acc_0) / 3

###############


5

0

1

###############


...

80.0

###############


38.88888888888889

54.166666666666664

73.33333333333333

In [ ]:
# save round
df.to_csv('../data/interactive_labeling_round_{}.csv'.format(m),
      sep='|',
      mode='w',
      encoding='utf-8',
      quoting=csv.QUOTE_NONNUMERIC,
      quotechar='\'')

In [ ]:
#df.loc[:10]

## Manual Labeling: ##

Find new threshold for labeling:

In [ ]:
threshold = 0.9997

n = 0
for max in maxima:
    if max < threshold:
        n += 1
n

In [ ]:
print('Number of articles with estimated probability < {}: {}'.format(threshold, len(df.loc[(df['Label'] == -1) & (df['Probability'] < threshold)])))

Check articles with probability under threshold:

In [ ]:
# pick articles with P < 0.99:
label_next = df.loc[(df['Label'] == -1) & (df['Probability'] < threshold), 'Index'].tolist()

In [ ]:
len(label_next)

In [ ]:
print('Estimated labels to be checked: class 0: {}, class 1: {}, class 2: {}'
      .format(len(df.loc[(df['Label'] == -1) & (df['Probability'] < threshold) & (df['Estimated'] == 0.0)]), 
              len(df.loc[(df['Label'] == -1) & (df['Probability'] < threshold) & (df['Estimated'] == 1.0)]),
              len(df.loc[(df['Label'] == -1) & (df['Probability'] < threshold) & (df['Estimated'] == 2.0)])))

In [ ]:
# increment round number
m += 1
print('This round number: {}'.format(m))

PLEASE READ THE FOLLOWING ARTICLES AND ENTER THE CORRESPONDING LABELS:

In [ ]:
for index in label_next:
    show_next(index)

In [ ]:
#df.loc[(df['Round'] == m) & (df['Index'].isin(label_next)), 'Round'] = m

In [ ]:
print('Number of manual labels in round no. {}:'.format(m))
print('0:{}, 1:{}, 2:{}'.format(len(df.loc[(df['Label'] == 0) & (df['Round'] == m)]), len(df.loc[(df['Label'] == 1) & (df['Round'] == m)]), len(df.loc[(df['Label'] == 2) & (df['Round'] == m)])))

print('Number of articles to be corrected in this round: {}'.format(len(df.loc[(df['Label'] != -1) & (df['Estimated'] != -1) & (df['Round'] == m) & (df['Label'] != df['Estimated'])])))

In [ ]:
# save intermediate status
df.to_csv('../data/interactive_labeling_round_{}_temp.csv'.format(m),
      sep='|',
      mode='w',
      encoding='utf-8',
      quoting=csv.QUOTE_NONNUMERIC,
      quotechar='\'')

## Resubstitution error: Multinomial Naive Bayes ##

In [ ]:
X_train_test = df.loc[df['Label'] != -1, 'Title'] + ' ' + df.loc[df['Label'] != -1, 'Text']
y_train_test = df.loc[df['Label'] != -1, 'Label']

In [ ]:
# discard old indices
y_train_test = y_train_test.reset_index(drop=True)
X_train_test = X_train_test.reset_index(drop=True)

In [ ]:
# use my own BagOfWords python implementation
stemming = True
rel_freq = True
extracted_words = BagOfWords.extract_all_words(X_train_test)
vocab = BagOfWords.make_vocab(extracted_words)

In [ ]:
# fit the training data and return the matrix
training_data = BagOfWords.make_matrix(extracted_words, vocab, rel_freq, stemming)
testing_data = training_data

In [ ]:
# Naive Bayes
classifier = MultinomialNB(alpha=1.0e-10, fit_prior=False, class_prior=None)

In [ ]:
# optional, nur bei resubstitutionsfehler

n = 0
for i in range(len(y_train_test)):
    if y_train_test[i] != predictions[i]:
        n += 1
        print('error no.{}'.format(n))
        print('prediction at index {} is: {}, but actual is: {}'.format(i, predictions[i], y_train_test[i]))
        print(X_train_test[i])
        print(y_train_test[i])
        print()
if n==0:
    print('no resubstitution error :-)')
else:
    print('number of wrong estimated articles: {}'.format(n))

In [ ]:
print('End of this round (no. {}):'.format(m))
print('Number of manually labeled articles: {}'.format(len(df.loc[df['Label'] != -1])))
print('Number of manually unlabeled articles: {}'.format(len(df.loc[df['Label'] == -1])))

In [ ]:
# save this round to csv
df.to_csv('../data/interactive_labeling_round_{}_neu.csv'.format(m),
      sep='|',
      mode='w',
      encoding='utf-8',
      quoting=csv.QUOTE_NONNUMERIC,
      quotechar='\'')

NOW PLEASE CONTINUE WITH PART II.
REPEAT UNTIL ALL SAMPLES ARE LABELED.